In [1]:
] add CSV

    Updating registry at `~/.julia/registries/General.toml`
   Resolving package versions...
  No Changes to `~/.julia/environments/v1.8/Project.toml`
  No Changes to `~/.julia/environments/v1.8/Manifest.toml`


In [2]:
] add DataFrames

   Resolving package versions...
  No Changes to `~/.julia/environments/v1.8/Project.toml`
  No Changes to `~/.julia/environments/v1.8/Manifest.toml`


In [3]:
using CSV
using DataFrames

In [4]:
alldata = CSV.read("data.csv", DataFrame);

In [5]:
size(alldata)

(20, 6)

In [6]:
data = alldata[5:end, :];

In [7]:
size(data)

(16, 6)

In [8]:
data.x

16-element Vector{Int64}:
 203
  58
 210
 202
 198
 158
 165
 201
 157
 131
 166
 160
 186
 125
 218
 146

In [9]:
using WGLMakie

In [10]:
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x, data.y, markersize=20, color=:red)
f

In [11]:
b_eye = 50.
m_eye = 2.
q_eye = .001;

In [12]:
xx = LinRange(50, 250, 20)

20-element LinRange{Float64, Int64}:
 50.0,60.5263,71.0526,81.5789,92.1053,…,207.895,218.421,228.947,239.474,250.0

In [13]:
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x, data.y, markersize=20, color=:red)

yy_eye = q_eye .* xx.^2 .+ xx .* m_eye .+ b_eye
lines!(xx, yy_eye)

f

In [14]:
] add Optim

   Resolving package versions...
  No Changes to `~/.julia/environments/v1.8/Project.toml`
  No Changes to `~/.julia/environments/v1.8/Manifest.toml`


In [15]:
using Optim

In [16]:
function objective(parameters)
    b = parameters[1]
    m = parameters[2]
    q = parameters[3]
    @show b, m
    return abs(b - 3.4) + abs(m - 17)
end

objective (generic function with 1 method)

In [17]:
function objective_2(parameters)
    b = parameters[1]
    m = parameters[2]
    q = parameters[3]

    y_pred = b .+ m .* data.x .+ q .* data.x.^2
    
    return sum(abs.(data.y .- y_pred))
end

objective_2 (generic function with 1 method)

In [18]:
starting_params = [b_eye + 0., m_eye, q_eye]
result = optimize(objective_2, starting_params)

 * Status: success

 * Candidate solution
    Final objective value:     3.339365e+02

 * Found with
    Algorithm:     Nelder-Mead

 * Convergence measures
    √(Σ(yᵢ-ȳ)²)/n ≤ 1.0e-08

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    192
    f(x) calls:    355


In [19]:
b_abs, m_abs, q_abs = Optim.minimizer(result)

3-element Vector{Float64}:
 94.76027385840413
  1.1092347687349888
  0.0041332073587093

In [20]:
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x, data.y, markersize=20, color=:red)

yy_eye = q_eye .* xx.^2 .+ xx .* m_eye .+ b_eye
lines!(xx, yy_eye, color=:orange)

yy_abs = q_abs .* xx.^2 .+ xx .* m_abs .+ b_abs
lines!(xx, yy_abs, color =: green)

f

In [21]:
function objective_gauss(parameters, x, y, sigma)
    b = parameters[1]
    m = parameters[2]
    q = parameters[3]

    y_pred = b .+ m .* x .+ q .* x.^2
    
    return -sum(
        -log.(sigma * sqrt(2 * π)) .-0.5 .* (y .- y_pred).^2 / sigma.^2)
end

objective_gauss (generic function with 1 method)

In [22]:
#function shim(p)
#    return objective_abs(p, data.x, data.y, data.sigma_y)
#end

In [23]:
starting_params = [b_eye + 0., m_eye, q_eye]
result = optimize(p -> objective_gauss(p, data.x, data.y, data.sigma_y),
                  starting_params)

 * Status: success

 * Candidate solution
    Final objective value:     1.044006e+03

 * Found with
    Algorithm:     Nelder-Mead

 * Convergence measures
    √(Σ(yᵢ-ȳ)²)/n ≤ 1.0e-08

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    83
    f(x) calls:    153


In [24]:
b_gauss, m_gauss, q_gauss = Optim.minimizer(result)

3-element Vector{Float64}:
 101.51680519707841
   1.112134650293423
   0.003790790491492483

In [25]:
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x, data.y, markersize=20, color=:red)

yy_eye = xx .* m_eye .+ b_eye .+ q_eye .* xx.^2
lines!(xx, yy_eye, color=:orange)

yy_abs = xx .* m_abs .+ b_abs .+ q_abs .* xx.^2
lines!(xx, yy_abs, color=:green)

yy_gauss = xx .* m_gauss .+ b_gauss .+ q_gauss .* xx.^2
lines!(xx, yy_gauss, color=:purple, linewidth=3)

f

In [26]:
@show data.x;

data.x = [203, 58, 210, 202, 198, 158, 165, 201, 157, 131, 166, 160, 186, 125, 218, 146]


In [27]:
size(data, 1)

16

In [28]:
ndata = size(data,1)

B_jack = zeros(ndata)
M_jack = zeros(ndata)
Q_jack = zeros(ndata)

for i in 1:ndata
    
    xcopy = copy(data.x)
    deleteat!(xcopy, i)

    ycopy = copy(data.y)
    deleteat!(ycopy, i)

    scopy = copy(data.sigma_y)
    deleteat!(scopy, i)

    starting_params = [b_eye + 0., m_eye, q_eye]
    result = optimize(p -> objective_gauss(p, xcopy, ycopy, scopy),
                      starting_params)
    @assert Optim.converged(result)
    b_jack, m_jack, q_jack = Optim.minimizer(result)
    
    B_jack[i] = b_jack
    M_jack[i] = m_jack 
    Q_jack[i] = q_jack
end

In [29]:
@assert 2+2 == 4

In [30]:
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x, data.y, markersize=20, color=:red)

for i in 1:ndata
    yy_jack = xx .* M_jack[i] .+ B_jack[i] .+ Q_jack[i] .* xx.^2
    lines!(xx, yy_jack, color=:green)
end

yy_gauss = xx .* m_gauss .+ b_gauss .+ q_gauss .* xx.^2
lines!(xx, yy_gauss, color=:purple, linewidth=3)

f

In [31]:
f = Figure()
Axis(f[1, 1])
scatter!(B_jack, M_jack, markersize=20, color=:red)

plot!([b_gauss], [m_gauss], markersize=30)

f

In [32]:
f = Figure()
Axis(f[1, 1])
scatter!(Q_jack, M_jack, markersize=20, color=:blue)
f

In [33]:
f = Figure()
Axis(f[1, 1])
scatter!(B_jack, Q_jack, markersize=20, color=:green)
f

I discussed this with some classmates and we determined that the correlation or anti-correlation in these plots isn't the important feature. Rather, what matters is how much the points are spread out. We think that the point that is very far away from all the others is the iteration of the jackknife analysis where the outlier was left out. Since it was left in for all of the other iterations, those values for m, b, and q are skewed but the one where it was pulled out is probably more representative of the dataset without the outlier.

In [34]:
function objective_gauss_linear(parameters, x, y, sigma)
    b = parameters[1]
    m = parameters[2]

    y_pred = b .+ m .* x 
    
    return -sum(
        -log.(sigma * sqrt(2 * π)) .-0.5 .* (y .- y_pred).^2 / sigma.^2)
end

objective_gauss_linear (generic function with 1 method)

In [35]:
# Range of m,b values to plot
bvals = LinRange(0, 60., 100)
mvals = LinRange(1., 2.7, 100);
# Compute the objective function for each point in a grid
og1 = [objective_gauss_linear([b,m], data.x[2:16], data.y[2:16], data.sigma_y[2:16])
      for b in bvals, m in mvals]

f = Figure()
Axis(f[1, 1])
contour!(bvals, mvals, og1, levels = 20)
#contour!(bvals, mvals, og2, levels = 20)
f

In [36]:
maximum!(og)

LoadError: UndefVarError: og not defined

In [37]:
using Statistics

In [38]:
mean(B_jack), std(B_jack) .* sqrt((ndata - 1) / ndata)

(118.24162709855082, 69.10728984297103)

In [39]:
mean(M_jack), std(M_jack) .* sqrt((ndata - 1) / ndata)

(0.9164465263685291, 0.8194971090255541)

In [40]:
mean(Q_jack), std(Q_jack) .* sqrt((ndata - 1) / ndata)

(0.004348479802542149, 0.0023765449920179907)

In [41]:
f = Figure()
Axis(f[1, 1])
errorbars!(alldata.x, alldata.y, alldata.sigma_y)
scatter!(alldata.x, alldata.y, markersize=20, color=:red)
f

In [42]:
starting_params = [b_eye + 0., m_eye, q_eye]
result = optimize(p -> objective_gauss(p, alldata.x, alldata.y, alldata.sigma_y),
                  starting_params)
@assert Optim.converged(result)
b_bad, m_bad, q_bad = Optim.minimizer(result)

3-element Vector{Float64}:
 322.61356256951655
   0.4509894771158308
   0.0005682575219269736

In [43]:
f = Figure()
Axis(f[1, 1])
errorbars!(alldata.x, alldata.y, alldata.sigma_y)
scatter!(alldata.x, alldata.y, markersize=20, color=:red)

yy_bad = xx .* m_bad .+ b_bad .+ q_bad .* xx.^2
lines!(xx, yy_bad, color=:purple, linewidth=3)

f

In [44]:
function objective_outliers(parameters, x, y, sigma)
    b = parameters[1]
    m = parameters[2]
    q = parameters[3]

    frac_bad = 0.01
    like_bad = frac_bad * (1. / 600.)

    y_pred = b .+ m .* x
    like_good = (1. - frac_bad) * 1 ./(sqrt(2*π) .* sigma) .* exp.(-0.5 * (y .- y_pred).^2 ./ sigma.^2)
    like = like_bad .+ like_good
    loglike = log.(like)

    return -sum(loglike)
end

objective_outliers (generic function with 1 method)

In [45]:
starting_params = [b_eye + 0., m_eye, q_eye]
result = optimize(p -> objective_outliers(p, alldata.x, alldata.y, alldata.sigma_y),
                  starting_params)
@assert Optim.converged(result)
b_out, m_out, q_out = Optim.minimizer(result)

3-element Vector{Float64}:
 32.71804459370706
  2.2526279323343017
  0.030196002763897018

In [46]:
starting_params = [700 + 0., -0.5, .4]
result = optimize(p -> objective_outliers(p, alldata.x, alldata.y, alldata.sigma_y),
                  starting_params)
@assert Optim.converged(result)
b_punk, m_punk, q_punk = Optim.minimizer(result)

3-element Vector{Float64}:
 627.9755452955544
  -0.7590163641858446
   0.38440880063438765

In [47]:
f = Figure()
Axis(f[1, 1])
errorbars!(alldata.x, alldata.y, alldata.sigma_y)
scatter!(alldata.x, alldata.y, markersize=20, color=:red)

yy_bad = xx .* m_bad .+ b_bad .+ q_bad .* xx .^2
lines!(xx, yy_bad, color=:purple, linewidth=3)

yy_out = xx .* m_out .+ b_out .+ q_out .* xx .^2
lines!(xx, yy_out, color=:green, linewidth=3)

yy_punk = xx .* m_punk .+ b_punk .+ q_punk .* xx .^2
lines!(xx, yy_punk, color=:blue, linewidth=3)

f

In [48]:
function objective_outliers(parameters, x, y, sigma)
    b = parameters[1]
    m = parameters[2]

    frac_bad = 0.01
    like_bad = frac_bad * (1. / 600.)

    y_pred = b .+ m .* x
    like_good = (1. - frac_bad) * 1 ./(sqrt(2*π) .* sigma) .* exp.(-0.5 * (y .- y_pred).^2 ./ sigma.^2)
    like = like_bad .+ like_good
    loglike = log.(like)

    return -sum(loglike)
end

objective_outliers (generic function with 1 method)

In [49]:
starting_params = [b_eye + 0., m_eye]
result = optimize(p -> objective_outliers(p, alldata.x, alldata.y, alldata.sigma_y),
                  starting_params)
@assert Optim.converged(result)
b_out, m_out = Optim.minimizer(result)

2-element Vector{Float64}:
 32.71335736732801
  2.252659398988028

In [50]:
starting_params = [700 + 0., -0.5]
result = optimize(p -> objective_outliers(p, alldata.x, alldata.y, alldata.sigma_y),
                  starting_params)
@assert Optim.converged(result)
b_punk, m_punk = Optim.minimizer(result)

2-element Vector{Float64}:
 627.9728284643311
  -0.7590088958472745

In [51]:
f = Figure()
Axis(f[1, 1])
errorbars!(alldata.x, alldata.y, alldata.sigma_y)
scatter!(alldata.x, alldata.y, markersize=20, color=:red)

yy_bad = xx .* m_bad .+ b_bad
lines!(xx, yy_bad, color=:purple, linewidth=3)

yy_out = xx .* m_out .+ b_out
lines!(xx, yy_out, color=:green, linewidth=3)

yy_punk = xx .* m_punk .+ b_punk
lines!(xx, yy_punk, color=:blue, linewidth=3)

f

In [52]:
# Range of m,b values to plot
bvals = LinRange(0, 60., 100)
mvals = LinRange(1., 2.7, 100);
# Compute the objective function for each point in a grid
og1 = [objective_outliers([b,m], data.x[2:16], data.y[2:16], data.sigma_y[2:16])
      for b in bvals, m in mvals]

f = Figure()
Axis(f[1, 1])
contour!(bvals, mvals, og1, levels = 20)
#contour!(bvals, mvals, og2, levels = 20)
f

In this section, I am going to reparametrize our fit so that m and b will not be correlated (problem 3).To do this, I will subtract the mean from the x values in data set and perform the fitting and jackknife procedure again.

In [53]:
x_shifted = data.x .- mean(data.x)

16-element Vector{Float64}:
   35.25
 -109.75
   42.25
   34.25
   30.25
   -9.75
   -2.75
   33.25
  -10.75
  -36.75
   -1.75
   -7.75
   18.25
  -42.75
   50.25
  -21.75

In [56]:
f = Figure()
Axis(f[1, 1])
errorbars!(x_shifted, data.y, data.sigma_y)
scatter!(x_shifted, data.y, markersize=20, color=:red)
f

In [72]:
b_eye_shifted = 400.
m_eye_shifted = 2.;

In [85]:
xx_shifted = LinRange(-120, 50, 20)

20-element LinRange{Float64, Int64}:
 -120.0,-111.053,-102.105,-93.1579,…,14.2105,23.1579,32.1053,41.0526,50.0

In [74]:
f = Figure()
Axis(f[1, 1])
errorbars!(x_shifted, data.y, data.sigma_y)
scatter!(x_shifted, data.y, markersize=20, color=:red)

yy_eye_shifted = xx .* m_eye_shifted .+ b_eye_shifted
lines!(xx, yy_eye_shifted)

f

In [78]:
ndata = size(data, 1)

B_jack_shifted = zeros(ndata)
M_jack_shifted = zeros(ndata)

for i in 1:ndata
    
    xcopy = copy(x_shifted)
    deleteat!(xcopy, i)

    ycopy = copy(data.y)
    deleteat!(ycopy, i)

    scopy = copy(data.sigma_y)
    deleteat!(scopy, i)

    starting_params = [b_eye_shifted + 0., m_eye_shifted]
    result = optimize(p -> objective_gauss_linear(p, xcopy, ycopy, scopy),
                      starting_params)
    @assert Optim.converged(result)
    b_jack_shifted, m_jack_shifted = Optim.minimizer(result)
    
    B_jack_shifted[i] = b_jack_shifted
    M_jack_shifted[i] = m_jack_shifted
end

In [87]:
function objective_gauss_linear(parameters, x, y, sigma)
    b = parameters[1]
    m = parameters[2]

    y_pred = b .+ m .* x
    
    return -sum(
        -log.(sigma * sqrt(2 * π)) .-0.5 .* (y .- y_pred).^2 / sigma.^2)
end

objective_gauss_linear (generic function with 1 method)

In [88]:
b_gauss_shifted, m_gauss_shifted = Optim.minimizer(result)

2-element Vector{Float64}:
 401.26531813703906
   2.2086638459235277

In [89]:
starting_params_shifted = [b_eye_shifted + 0., m_eye_shifted]
result_shifted = optimize(p -> objective_gauss_linear(p, data.x, data.y, data.sigma_y),
                  starting_params)

 * Status: success

 * Candidate solution
    Final objective value:     1.044426e+03

 * Found with
    Algorithm:     Nelder-Mead

 * Convergence measures
    √(Σ(yᵢ-ȳ)²)/n ≤ 1.0e-08

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    40
    f(x) calls:    80


In [92]:
yy_gauss_shifted = xx_shifted .* m_gauss_shifted .+ b_gauss_shifted

20-element LinRange{Float64, Int64}:
 136.226,155.987,175.749,195.511,215.273,…,452.413,472.175,491.937,511.699

In [93]:
f = Figure()
Axis(f[1, 1])
errorbars!(x_shifted, data.y, data.sigma_y)
scatter!(x_shifted, data.y, markersize=20, color=:red)

for i in 1:ndata
    yy_jack_shifted = xx_shifted .* M_jack_shifted[i] .+ B_jack_shifted[i] 
    lines!(xx_shifted, yy_jack_shifted, color=:green)
end

yy_gauss = xx_shifted .* m_gauss_shifted .+ b_gauss_shifted 
lines!(xx_shifted, yy_gauss_shifted, color=:purple, linewidth=3)

f 

In [94]:
ndata = size(data,1)

B_jack = zeros(ndata)
M_jack = zeros(ndata)

for i in 1:ndata
    
    xcopys = copy(x_shifted)
    deleteat!(xcopys, i)

    ycopy = copy(data.y)
    deleteat!(ycopy, i)

    scopy = copy(data.sigma_y)
    deleteat!(scopy, i)

    starting_params = [b_eye_shifted + 0., m_eye_shifted]
    result_shifted = optimize(p -> objective_gauss_linear(p, xcopys, ycopy, scopy),
                      starting_params)
    @assert Optim.converged(result_shifted)
    b_jack_shifted, m_jack_shifted = Optim.minimizer(result_shifted)
    
    B_jack_shifted[i] = b_jack_shifted
    M_jack_shifted[i] = m_jack_shifted
end

In [95]:
f = Figure()
Axis(f[1, 1])
errorbars!(x_shifted, data.y, data.sigma_y)
scatter!(x_shifted, data.y, markersize=20, color=:red)

for i in 1:ndata
    yy_jack_shifted = xx_shifted .* M_jack_shifted[i] .+ B_jack_shifted[i] .+ Q_jack_shifted[i] .* xx.^2
    lines!(xx_shifted, yy_jack_shifted, color=:green)
end

yy_gauss_shifted = xx .* m_gauss_shifted .+ b_gauss_shifted
lines!(xx_shifted, yy_gauss_shifted, color=:purple, linewidth=3)

f

In [99]:
f = Figure()
Axis(f[1, 1])
scatter!(B_jack_shifted, M_jack_shifted, markersize=20, color=:red)

plot!([b_gauss_shifted], [m_gauss_shifted], markersize=30)

f

In [98]:
# Range of m,b values to plot
bvals = LinRange(0, 60., 100)
mvals = LinRange(1., 2.7, 100);
# Compute the objective function for each point in a grid
og1 = [objective_gauss_linear([b,m], x_shifted[2:16], data.y[2:16], data.sigma_y[2:16])
      for b in bvals, m in mvals]

f = Figure()
Axis(f[1, 1])
contour!(bvals, mvals, og1, levels = 20)
#contour!(bvals, mvals, og2, levels = 20)
f

Since we just shifted the x values by a constant, m_shifted = m and b = -m_shifted * x_avg + b. 

In [105]:
B_jack_shiftedback =  m_gauss_shifted * mean(data.x) .+ B_jack_shifted
b_gauss_shiftedback = m_gauss_shifted* mean(data.x) .+ b_gauss_shifted
f = Figure()
Axis(f[1, 1])
scatter!(B_jack_shiftedback, M_jack_shifted, markersize=20, color=:red)

plot!([b_gauss_shiftedback], [m_gauss_shifted], markersize=30)

f

This is an interesting finding -- once we shift the m and b values back we still have no correlation between.

# Stretch 1

Chi square is a type of hypothesis testing is primarily used to determine whether two variables are independent in influencing the test statistic. In this case, we want to use it to determine whether adding a quadratic term improves the fit, because if q doesn't independently influence the 